In [1]:
import requests
import pandas as pd
from datetime import datetime
from tqdm import tqdm

BINANCE_CANDLE_COLUMNS = ['opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime',
                          'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

def binance_recursive_fetch_2(coins, interval, starttime, endtime, data_type='spot'):
    all_coins_result = {}
    data_list = []
    call_dict = {}
    
    for coin in tqdm(coins):
        result_list = []
        current_time = starttime
        call = 0
        timestamps = []
        
        while current_time < endtime:
            if ((int((endtime - current_time) / (1000 * 60))) + 1) >= 1000:
                limit = 1000
            else:
                limit = int((endtime - current_time) / (1000 * 60) + 1)
            
            if data_type == 'spot':
                url = (f'https://api.binance.com/api/v3/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            elif data_type == 'futures':
                url = (f'https://fapi.binance.com/fapi/v1/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            
            result_list += requests.get(url).json()
            
            if result_list:
                # Update current_time with the timestamp of the last data point fetched, plus 1 minute (60000 ms)
                current_time = result_list[-1][0] + 60000
                timestamps.append(current_time)
                call += 1
                
                # Check if the last fetched timestamp is greater than or equal to endtime
                if current_time >= endtime:
                    print(f"Reached endtime at {datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')}. Stopping fetch.")
                    break
                
                print((datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')) + 
                      f' status : {current_time < endtime}, time : {current_time}, limit : {call * 2}')
            
            # Ensure there's no continuous fetching of the same timestamp
            if len(timestamps) > 1 and timestamps[-1] == timestamps[-2]:
                print("Duplicate timestamp detected. Stopping fetch.")
                break
            
            # Sleep if needed to avoid rate limiting (adjust based on your rate limit)
            # time.sleep(0.1)  # Uncomment if needed
            
        current_df = pd.DataFrame(result_list, columns=BINANCE_CANDLE_COLUMNS)
        current_df['coin'] = coin
        current_df = current_df[['coin'] + BINANCE_CANDLE_COLUMNS]
        current_df = current_df.values.tolist()
        
        data_list += current_df
        call_dict.update({coin: call})
    
    return {'data': data_list, 'call': call_dict}

# Set endtime to the current time (today)
endtime = int(datetime.utcnow().timestamp() * 1000)

# # Example usage with today's date as the end time
# sample_spot = binance_recursive_fetch_2(
#     ['USDT'],
#     '1m',
#     starttime=int(pd.to_datetime('2023-01-01 00:00', utc=True).timestamp() * 1000),
#     endtime=endtime,
#     data_type='spot'  # Fetch spot data
# )

# print(sample_spot['data'])

C:\Users\user\AppData\Local\Temp\ipykernel_6768\3312417040.py:74: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  endtime = int(datetime.utcnow().timestamp() * 1000)


In [2]:
# Fetch NEAR USDT
sample_spot = binance_recursive_fetch_2(
    ['XRP'],
    '1h',
    starttime=int(pd.to_datetime('2020-01-01 00:00', utc=True).timestamp() * 1000),
    endtime=endtime,
    data_type='futures'  # Fetch spot data
)

print(sample_spot['data'])

  0%|          | 0/1 [00:00<?, ?it/s]

2020-02-17 07:01:00 status : True, time : 1581894060000, limit : 2
2020-03-29 23:01:00 status : True, time : 1585494060000, limit : 4
2020-05-10 15:01:00 status : True, time : 1589094060000, limit : 6
2020-06-21 07:01:00 status : True, time : 1592694060000, limit : 8
2020-08-01 23:01:00 status : True, time : 1596294060000, limit : 10
2020-09-12 15:01:00 status : True, time : 1599894060000, limit : 12
2020-10-24 07:01:00 status : True, time : 1603494060000, limit : 14
2020-12-04 23:01:00 status : True, time : 1607094060000, limit : 16
2021-01-15 15:01:00 status : True, time : 1610694060000, limit : 18
2021-02-26 07:01:00 status : True, time : 1614294060000, limit : 20
2021-04-08 23:01:00 status : True, time : 1617894060000, limit : 22
2021-05-20 15:01:00 status : True, time : 1621494060000, limit : 24
2021-07-01 07:01:00 status : True, time : 1625094060000, limit : 26
2021-08-11 23:01:00 status : True, time : 1628694060000, limit : 28
2021-09-22 15:01:00 status : True, time : 1632294060

100%|██████████| 1/1 [00:30<00:00, 30.17s/it]

Reached endtime at 2024-12-24 17:01:00. Stopping fetch.
[['XRP', 1578297600000, '0.1970', '0.2041', '0.1970', '0.2041', '6306.4', 1578301199999, '1243.65622', 4, '194.8', '39.67102', '0'], ['XRP', 1578301200000, '0.2013', '0.2222', '0.2004', '0.2127', '6676329.3', 1578304799999, '1388223.65941', 1406, '2537247.0', '530526.06882', '0'], ['XRP', 1578304800000, '0.2127', '0.2198', '0.2105', '0.2146', '3681788.3', 1578308399999, '790707.49646', 1304, '2512347.1', '539756.55003', '0'], ['XRP', 1578308400000, '0.2146', '0.2173', '0.2120', '0.2130', '3631936.0', 1578311999999, '778171.70592', 1520, '1778667.6', '382328.99033', '0'], ['XRP', 1578312000000, '0.2130', '0.2180', '0.2123', '0.2150', '4682254.3', 1578315599999, '1005779.46088', 1657, '2383415.4', '511753.61531', '0'], ['XRP', 1578315600000, '0.2150', '0.2160', '0.2108', '0.2120', '4161963.4', 1578319199999, '891053.34600', 1820, '1474779.6', '315767.57670', '0'], ['XRP', 1578319200000, '0.2120', '0.2152', '0.2109', '0.2132', '52272

In [3]:
# Define the column names for the DataFrame based on the Binance API response structure
columns = ['coin', 'opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime', 
           'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

# Convert the list of data into a DataFrame
df = pd.DataFrame(sample_spot['data'], columns=columns)

# Show the first few rows of the DataFrame
df

coin       opentime openprice highprice lowprice closeprice      volume  \
0      XRP  1578297600000    0.1970    0.2041   0.1970     0.2041      6306.4   
1      XRP  1578301200000    0.2013    0.2222   0.2004     0.2127   6676329.3   
2      XRP  1578304800000    0.2127    0.2198   0.2105     0.2146   3681788.3   
3      XRP  1578308400000    0.2146    0.2173   0.2120     0.2130   3631936.0   
4      XRP  1578312000000    0.2130    0.2180   0.2123     0.2150   4682254.3   
...    ...            ...       ...       ...      ...        ...         ...   
43533  XRP  1735016400000    2.2625    2.2659   2.2536     2.2564  18152576.2   
43534  XRP  1735020000000    2.2564    2.2579   2.2316     2.2358  20419599.5   
43535  XRP  1735023600000    2.2358    2.2506   2.2278     2.2463  19133339.0   
43536  XRP  1735027200000    2.2463    2.2596   2.2373     2.2514  23683666.7   
43537  XRP  1735030800000    2.2514    2.2544   2.2289     2.2346  13502354.6   

           closetime     quotevolume  trades taker_buy_volume taker_buy_quote  \
0      1578301199999      1243.65622       4            194.8        39.67102   
1      1578304799999   1388223.65941    1406        2537247.0    530526.06882   
2      1578308399999    790707.49646    1304        2512347.1    539756.55003   
3      1578311999999    778171.70592    1520        1778667.6    382328.99033   
4      1578315599999   1005779.46088    1657        2383415.4    511753.61531   
...              ...             ...     ...              ...             ...   
43533  1735019999999  41022688.80586   75235        8534193.2  19289229.90276   
43534  1735023599999  45878068.22651   81501        9202525.8  20678543.44445   
43535  1735027199999  42865112.41072   79741       10655610.6  23871307.20925   
43536  1735030799999  53319082.23619   93442       11963242.4  26939761.54782   
43537  1735034399999  30219717.55318   43425        6671723.6  14927807.13879   

      unused  
0          0  
1          0  
2          0  
3          0  
4          0  
...      ...  
43533      0  
43534      0  
43535      0  
43536      0  
43537      0  

[43538 rows x 13 columns]

In [4]:
df.to_csv('XRP_USDT_futures_data_2020.csv', index=False)

print("DataFrame has been saved to csv")

DataFrame has been saved to csv
